In [1]:
using Pkg, Revise
Pkg.activate("..")

  Activating project at `~/projects/MDPPricing`


In [2]:
include("../src/MDPPricing.jl")

Main.MDPPricing

In [8]:
using PMDPs
using POMDPs

using StaticArrays
using Distributions
using Plots
using Distributions
using DiscreteValueIteration
using Printf

using D3Trees
using AbstractTrees
using Colors

In [4]:
function simple_pp()
    T=8
    P = [
        PMDPs.Product([true, false], T-2), # 1
        PMDPs.Product([false, true], T), # 2
        PMDPs.Product([true, true], T-2),
    ]  # 3
    C₀ = [2, 2]
    D = BernoulliScheme(T, [0.08, 0.12, 0.06])
#     β₁ = DiscreteNonParametric([0.0, 5.0, 10.0 ], [0.1, 0.6, 0.3])
#     β₂ = DiscreteNonParametric([0.0, 5.0, 10.0, 15.0, 20.0], [0.1, 0.2, 0.4, 0.2, 0.1])
    β₁ = Normal(16, 5)
    β₂ = Normal(3, 2)
    B = [β₁, β₁, β₂]
    A = collect(0.:1.:25.) #[0.0, 5.0, 10.0, 15.0, 20.0]
    objective = :revenue

    pp = PMDPs.PMDPProblem(P, C₀, D, B, A, objective)
end

function super_simple_pp()
    T = 3
    P = [PMDPs.Product([true], T),]
    C₀ = [1,]
    D = BernoulliScheme(T, [0.1])
    β = DiscreteNonParametric([5.0, 10.0], [0.6, 0.4])
    B = [β] # budgets
    A = [0.0, 5.0, 10.0]
    objective = :revenue

    pp = PMDPs.PMDPProblem(P, C₀, D, B, A, objective)
end

pp = simple_pp();
mg, me = PMDPs.PMDPg(pp), PMDPs.PMDPe(pp);

solver = SparseValueIterationSolver(max_iterations = 100, belres = 1e-3, verbose = true)#, init_util=init_util) # creates the solver
# POMDPs.@show_requirements POMDPs.solve(solver, mdp)
policy = DiscreteValueIteration.solve(solver, me);

┌ Info: residual: 9.457735216999936, time: 0.0003183, total time: 0.0003183 
│   i = 1
└ @ DiscreteValueIteration /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/sparse.jl:75
┌ Info: residual: 1.981547043400023, time: 0.0003437, total time: 0.000662 
│   i = 2
└ @ DiscreteValueIteration /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/sparse.jl:75
┌ Info: residual: 1.981547043400023, time: 0.0003139, total time: 0.0009759 
│   i = 3
└ @ DiscreteValueIteration /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/sparse.jl:75
┌ Info: residual: 1.9565118370276515, time: 0.0002739, total time: 0.0012498000000000001 
│   i = 4
└ @ DiscreteValueIteration /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/sparse.jl:75
┌ Info: residual: 1.9150344481875425, time: 0.0003273, total time: 0.0015771000000000001 
│   i = 5
└ @ DiscreteValueIteration /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/sparse.jl:75
┌ Info: residual: 1.085962490680597

In [5]:
s₀ = rand(initialstate(me))

c:[2, 2]_t:1_p:4

In [6]:
module MyTrees
    using PMDPs
    using POMDPs

    struct Node
        s::PMDPs.State
        me::PMDPs.PMDPe
        policy::Policy
        parent::PMDPs.State
        prob::Float64
    end
end

Main.MyTrees

In [7]:
# Action Colormap
# first action is 0., last is reject (-1)
# first color is too white, ignore it (2:end)
CMAPₐ = colormap("Purples",length(actions(me))-1; logscale=false)[2:end] 
display(CMAPₐ)

# Products Colormap
CMAPₚ = colormap("Greens",length(me.pp.c₀)+1; logscale=false)[2:end] 
display(CMAPₚ)

In [8]:
function AbstractTrees.children(o::MyTrees.Node)
    a = action(o.policy, o.s)
    trans_distribution = transition(o.me, o.s, a)
    [MyTrees.Node(s, o.me, o.policy, o.s, prob) for (s, prob) in trans_distribution]
end


# Link color <-> Product size 
# Link width <-> probability
function D3Trees.link_style(o::MyTrees.Node)
    if o.s.iₚ==PMDPs.empty_product_id(o.me)
        style=""
    else
        product_size = sum(PMDPs.product(o.me, o.s))
        style= "stroke:#$(hex(CMAPₚ[product_size]))"
    end
    
    width = o.prob ==0. ? "0" : @sprintf("%.0f", maximum([1,o.prob*10]))
    style*=";stroke-width:$(width)px"
    
    if o.s.c == o.parent.c
       style*=";stroke-dasharray:3,3" 
    end
    
    return style
end

function D3Trees.style(o::MyTrees.Node)
    a =  action(o.policy, o.s)
    if a == 0.
        style="fill:#$(hex(colorant"lightgreen"))"
    elseif a == PMDPs.REJECT_ACTION
        style= "fill:#$(hex(colorant"red"))"
    else
        iₐ = findfirst(x->x==a, actions(me))
        style = "fill:#$(hex(CMAPₐ[iₐ-1]))"
    end
    return style
end

## Things that make printing prettier
function D3Trees.tooltip(o::MyTrees.Node)
    s = o.s
    p = PMDPs.product(o.me, s)
    a = action(o.policy, o.s)
    if p == PMDPs.empty_product(me)
        ps = "∅"
    else
        ps = "$(p)"[5:end]
    end
    prob = o.prob==0. ? "∅" : @sprintf("%.2f", o.prob)
    "P:$(prob), t:$(s.t), iₚ:$(s.iₚ), A:$(a)\nc:$(s.c)\np:$(ps)"
end

function D3Trees.text(o::MyTrees.Node)
    ""
end

In [9]:
o₀ = MyTrees.Node(s₀, me, policy, s₀, 1.)
# print_tree(o₀)
D3Tree(o₀)

(8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)


 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)


 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (4 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (4 children)
 (4 children)
 (4 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)


 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)
 (8 children)
 (8 children)
 (8 children)
 (4 children)

 (8 children)
 (8 children)
 (8 children)
 (4 children)

In [104]:
policy = PMDPs.get_VI_policy(me);

In [20]:
typeof(policy)

DiscreteValueIteration.ValueIterationPolicy{Matrix{Float64}, Vector{Float64}, Vector{Int64}, Float64, PMDPs.PMDPe}

In [26]:
?locals

search: locals task_local_storage local LocationScale



No documentation found.

`DiscreteValueIteration.locals` is a `Function`.

```
# 1 method for generic function "locals":
[1] locals(p::ValueIterationPolicy) in DiscreteValueIteration at /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/common.jl:67
```


In [ ]:
policy.

In [28]:
policy.action_map

5-element Vector{Float64}:
  0.0
  5.0
 10.0
 15.0
  1.7976931348623157e308

In [27]:
policy.util

12-element Vector{Float64}:
 0.0
 5.0
 0.0
 5.0
 0.0
 0.0
 0.0
 0.49500000000000005
 0.0
 0.0
 0.0
 0.0

In [25]:
locals(policy)

([0.0 0.0 … 0.0 0.0; 0.0 5.0 … 0.49500000000000005 0.49500000000000005; … ; 0.0 0.0 … 0.0 0.0; 0.0 0.0 … 0.0 0.0], [0.0, 5.0, 0.0, 5.0, 0.0, 0.0, 0.0, 0.49500000000000005, 0.0, 0.0, 0.0, 0.0], [1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1], [0.0, 5.0, 10.0, 15.0, 1.7976931348623157e308])

In [22]:
methodswith(typeof(policy); supertypes=true)

[1] action(p::POMDPPolicies.SoftmaxPolicy, on_policy::Policy, k, s) in POMDPPolicies at /home/mrkos/.julia/packages/POMDPPolicies/wMOK3/src/exploration_policies.jl:119
[2] action(policy::DiscreteValueIteration.ValueIterationPolicy, s::S) where S in DiscreteValueIteration at /home/mrkos/.julia/packages/DiscreteValueIteration/FjeJj/src/common.jl:71
[3] action(p::POMDPPolicies.EpsGreedyPolicy, on_policy::Policy, k, s) in POMDPPolicies at /home/mrkos/.julia/packages/POMDPPolicies/wMOK3/src/exploration_policies.jl:73
[4] simulate(sim::POMDPSimulators.RolloutSimulator, mdp::MDP, policy::Policy) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:141
[5] simulate(sim::POMDPSimulators.RolloutSimulator, mdp::MDP{S}, policy::Policy, initialstate::S) where S in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:146
[6] simulate(sim::POMDPSimulators.RolloutSimulator, m::MDP, p::Policy, is) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:186
[7] simulate(sim::POMDPSimulators.RolloutSimulator, pomdp::POMDP, policy::Policy) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:55
[8] simulate(sim::POMDPSimulators.RolloutSimulator, pomdp::POMDP, policy::Policy, bu::Updater) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:55
[9] simulate(sim::POMDPSimulators.RolloutSimulator, pomdp::POMDP{S}, policy::Policy, updater::Updater, initial_belief) where S in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:66
[10] simulate(sim::POMDPSimulators.RolloutSimulator, pomdp::POMDP, policy::Policy, updater::Updater, initial_belief, s) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:85
[11] simulate(sim::POMDPSimulators.RolloutSimulator, m::POMDP{S}, policy::Policy, initialstate::S) where S in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/rollout.jl:182
[12] simulate(sim::POMDPSimulators.StepSimulator, pomdp::POMDP, policy::Policy) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:19
[13] simulate(sim::POMDPSimulators.StepSimulator, pomdp::POMDP, policy::Policy, bu::Updater) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:19
[14] simulate(sim::POMDPSimulators.StepSimulator, pomdp::POMDP, policy::Policy, bu::Updater, dist) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:24
[15] simulate(sim::POMDPSimulators.StepSimulator, pomdp::POMDP, policy::Policy, bu::Updater, dist, is) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:24
[16] simulate(sim::POMDPSimulators.StepSimulator, mdp::MDP{S}, policy::Policy) where S in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:13
[17] simulate(sim::POMDPSimulators.StepSimulator, mdp::MDP{S}, policy::Policy, init_state::S) where S in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/stepthrough.jl:13
[18] simulate(sim::POMDPSimulators.HistoryRecorder, mdp::MDP{S, A}, policy::Policy) where {S, A} in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/history_recorder.jl:133
[19] simulate(sim::POMDPSimulators.HistoryRecorder, mdp::MDP{S, A}, policy::Policy, init_state::S) where {S, A} in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/history_recorder.jl:133
[20] simulate(sim::POMDPSimulators.HistoryRecorder, pomdp::POMDP, policy::Policy) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/history_recorder.jl:57
[21] simulate(sim::POMDPSimulators.HistoryRecorder, pomdp::POMDP, policy::Policy, bu::Updater) in POMDPSimulators at /home/mrkos/.julia/packages/POMDPSimulators/zxTz3/src/history_recorder.jl:57
[22] simulate(sim::POMDPSimulators.HistoryRecorder, pomd